<a href="https://colab.research.google.com/github/rdaniello/DataVizFall2020_Colab/blob/master/Learning_tooltips.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [14]:
import pandas as pd
import folium
import numpy as np
import json
import requests

In [2]:
# https://github.com/nytimes/covid-19-data repository location
db = "https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-counties.csv"
df = pd.read_csv(db)
df.head(1)

df['date'] = pd.to_datetime(df['date'])
df.dtypes

date      datetime64[ns]
county            object
state             object
fips             float64
cases              int64
deaths             int64
dtype: object

In [3]:
# function to filter by date and group and sum by state
def covid_stat_on(df,strDate, m_type):
    # date filter
    df_temp = df[df['date']==strDate][['state', m_type]].copy().dropna().reset_index(drop=True)

    # state sum
    df_temp = df_temp.groupby(by=['state']).sum()
    df_temp['state_name'] = df_temp.index

    # use log of cases total
    df_temp['cases'] = np.log(df_temp[m_type])
                                    
    return df_temp

covid_stat_on(df,'2020-9-15', 'deaths').head(1)

/usr/local/lib/python3.6/dist-packages/pandas/core/series.py:679: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


deaths state_name     cases
state                               
Alabama    2387    Alabama  7.777793

In [24]:
# the GEOJSON file
cb_2018_us_state_5m = "https://raw.githubusercontent.com/rdaniello/DataVizFall2020_Colab/master/cb_2018_us_state_5m.json"

tmp_f = pd.read_json(cb_2018_us_state_5m)

resp=requests.get(cb_2018_us_state_5m)
cb_2018_us_state_5m_fixed = json.loads(resp.text)

for feature in data['features']:
  feature['properties']['myval'] = 0

fff = data['features'][0]

print (fff)

zzz = json.dumps(data)

print(zzz)

{'type': 'Feature', 'geometry': {'type': 'Polygon', 'coordinates': [[[-104.053127, 43.000585], [-104.052863, 42.754569], [-104.052809, 42.749966], [-104.052583, 42.650062], [-104.052741, 42.633981999999996], [-104.052586, 42.630917], [-104.052773275295, 42.611766367052894], [-104.052775, 42.61159], [-104.052775, 42.610813], [-104.053107, 42.499964], [-104.052776, 42.25822], [-104.052793, 42.249962], [-104.053125, 42.249962], [-104.052761, 42.170277999999996], [-104.052547, 42.166801], [-104.053001, 42.137254], [-104.052738, 42.133769], [-104.0526, 42.124963], [-104.052954, 42.089076999999996], [-104.052966926101, 42.075083999008], [-104.052967, 42.075004], [-104.05288, 42.021761], [-104.052729, 42.016318], [-104.052704176933, 42.0017178993875], [-104.052699, 41.998673], [-104.052761, 41.994966999999995], [-104.05283, 41.994600000000005], [-104.052856, 41.975958], [-104.052734, 41.973006999999996], [-104.052991, 41.914972999999996], [-104.052931, 41.906143], [-104.053026, 41.885464], [-

In [32]:
df_cases=

#Map object 
m = folium.Map(
            location=[48, -102], # center the map to this point
            zoom_start=4)        # starting zoom!

#Choropleth layer - data function returns log of cases
folium.Choropleth(
    geo_data=cb_2018_us_state_5m, ## load the downloaded GeoJSON (mapshaper.org converted)
    name='Covid-19 State Cases',          ## add a name for the layer
    legend_name='Actual State Covid-19 Cases (log)',  ## add legend topic
    data=covid_stat_on(df,'2020-9-13', 'cases'),   ## pass our covid-19 data to the layer method
    columns=['state_name','cases'],             ## the columns from our data
    key_on='feature.properties.NAME',    ## the state
    fill_color='YlOrRd',                    ## color style BuGn, BuPu, GnBu, OrRd, PuBu, PuBuGn, PuRd, RdPu, YlGn, YlGnBu, YlOrBr, and YlOrRd
    bins=9,                               ## number of bins usef of color codding 
    fill_opacity=0.7,
    line_opacity=0.2,
    nan_fill_color='blue',
    highlight=True,
    show=False
).add_to(m)

choropleth = folium.Choropleth(
    geo_data=zzz,
    name='Covid-19 State Deaths',
    legend_name='Actual State Covid-19 Deaths (log)',
    data=covid_stat_on(df,'2020-9-13', 'deaths'),
    columns=['state_name','deaths'],
    key_on='feature.properties.NAME',
    fill_color='YlGnBu',
    bins=9,
    fill_opacity=0.7,
    line_opacity=0.2,
    nan_fill_color='none',
    highlight=True,
     show=True).add_to(m)

choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(
        fields=['NAME', 'myval'], 
        aliases=['State', 'Deaths'],
        labels=True)
)

folium.LayerControl().add_to(m)

m

/usr/local/lib/python3.6/dist-packages/pandas/core/series.py:679: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)


In [6]:
m.save('index.html')